In [16]:
import pandas as pd
import numpy as np
import math

## 1. Preprocess datasets

In [17]:
# Two types of nodes relations
relations_dict={'Activation':'-->','Inhibition':'--|'}
relations_dict

{'Activation': '-->', 'Inhibition': '--|'}

### 1.1. GSE2034

In [190]:
gse2034_raw = pd.read_csv('Data/GSE2034.zip', compression='zip', header=0, sep='\t', quotechar='"')
gse2034=gse2034_raw.copy()

# preprocess dataset
gse2034[['Gene','KEGG-ID']] = gse2034['Class'].str.split('#',expand=True)
gse2034.drop('Class', inplace=True, axis=1)
cols = gse2034.columns.tolist()
cols = cols[-2:] + cols[:-2]
gse2034=gse2034[cols]

gse2034

Gene        KEGG-ID   ERpos  ERpos.1  ERpos.2  \
0                        1007_s_at  hsa:100616237  3848.1   6520.9   5285.7   
1                        1007_s_at        hsa:780  3848.1   6520.9   5285.7   
2                          1053_at       hsa:5982   228.9    112.5    178.4   
3                           117_at       hsa:3310   213.1    189.8    269.7   
4                           121_at       hsa:7849  1009.4   2083.3   1203.4   
...                            ...            ...     ...      ...      ...   
22640   AFFX-HUMISGF3A/M97935_3_at       hsa:6772  2908.8   6087.7   4264.5   
22641   AFFX-HUMISGF3A/M97935_5_at       hsa:6772    29.8     16.1     96.3   
22642  AFFX-HUMISGF3A/M97935_MA_at       hsa:6772   403.9     79.3    837.3   
22643  AFFX-HUMISGF3A/M97935_MB_at       hsa:6772   389.9    274.5    937.3   
22644      AFFX-HUMRGE/M10098_5_at     hsa:649159   802.5    247.8   2297.5   

        ERneg  ERpos.3  ERpos.4  ERpos.5  ERpos.6  ...  ERneg.72  ERneg.73  \
0      4043.7   4263.6   2949.8   5498.9   3863.1  ...    4058.2    4017.6   
1      4043.7   4263.6   2949.8   5498.9   3863.1  ...    4058.2    4017.6   
2       398.7    417.7    221.2    280.4    198.2  ...     183.4     356.1   
3       312.4    327.1    225.0    243.5    244.4  ...     326.6     234.9   
4      1104.4   1043.3   1117.6   1085.4   1423.1  ...    1041.3    1195.6   
...       ...      ...      ...      ...      ...  ...       ...       ...   
22640  3496.5   3952.3   1585.9   1396.4   2782.3  ...    1074.5    2120.3   
22641    71.1     36.6     26.1      8.8     64.7  ...      26.9     108.7   
22642  1024.2    969.1    205.4    388.2    423.0  ...      40.6     263.3   
22643   982.5    656.3    371.9    283.1    765.2  ...      71.9     293.9   
22644   807.1    141.4    269.3     93.6    238.1  ...    1702.7     412.4   

       ERneg.74  ERneg.75  ERpos.204  ERpos.205  ERpos.206  ERpos.207  \
0        2841.0    2914.2     3681.0     3066.9     2773.0     2984.3   
1        2841.0    2914.2     3681.0     3066.9     2773.0     2984.3   
2         234.6     169.4       94.5      265.5      209.8      160.0   
3         369.6     149.5      236.4      347.9      226.7      252.9   
4         751.5    1117.8     1022.4     1127.4     1071.8     1178.5   
...         ...       ...        ...        ...        ...        ...   
22640    1548.9    1460.8     2515.1     3991.3     1361.4     1917.7   
22641      43.5      23.4       53.7       46.7       11.1       33.1   
22642     136.2      27.5       92.1      399.2      143.1      119.7   
22643     363.9     124.8      186.6      329.5      281.9      295.9   
22644    1146.6     410.9      417.4      413.1      231.2      269.2   

       ERneg.76  ERpos.208  
0        3540.0     2620.0  
1        3540.0     2620.0  
2         285.7      180.5  
3         135.1      191.8  
4        1256.7     1284.6  
...         ...        ...  
22640    1880.2     2040.0  
22641       8.4       12.0  
22642     533.8      172.4  
22643     491.1      150.0  
22644     113.0      298.0  

[22645 rows x 288 columns]

In [168]:
# Change column names
labels=gse2034.columns[2:]
for x in range(len(labels)):
    if(labels[x].startswith('ERpos')):
        labels.values[x]="ERpos"
    elif(labels[x].startswith('ERneg')):
        labels.values[x]="ERneg"

In [169]:
# Get the genes that are present in the GSE2034 dataset and create a dictionary 
# where the keys are the genes and the values are the corresponding KEGG-IDs
# 'a gene can be mapped to more than one Entrez identifier'
gene_list=sorted(set(gse2034['Gene'].tolist()))
gene_dict={}
for i in gene_list:
    tmp=gse2034.loc[gse2034['Gene'] == i]['KEGG-ID']
    tmp_list=[]
    for t in tmp:
        tmp_list.append(t)
    gene_dict.update({i:tmp_list})
print('Gene dictionary (key: Genes, values: KEGG-IDs): '+str(gene_dict))

Gene dictionary (key: Genes, values: KEGG-IDs): {'1007_s_at': ['hsa:100616237', 'hsa:780'], '1053_at': ['hsa:5982'], '117_at': ['hsa:3310'], '121_at': ['hsa:7849'], '1255_g_at': ['hsa:2978'], '1294_at': ['hsa:7318'], '1316_at': ['hsa:7067'], '1320_at': ['hsa:11099'], '1405_i_at': ['hsa:6352'], '1431_at': ['hsa:1571'], '1438_at': ['hsa:2049'], '1487_at': ['hsa:2101'], '1494_f_at': ['hsa:1548'], '1598_g_at': ['hsa:2621'], '160020_at': ['hsa:4323'], '1729_at': ['hsa:8717'], '1773_at': ['hsa:100529261', 'hsa:2342'], '177_at': ['hsa:5337'], '179_at': ['hsa:441263'], '1861_at': ['hsa:572'], '200000_s_at': ['hsa:10594'], '200001_at': ['hsa:826'], '200002_at': ['hsa:11224'], '200003_s_at': ['hsa:6158'], '200004_at': ['hsa:1982'], '200005_at': ['hsa:8664'], '200006_at': ['hsa:11315'], '200007_at': ['hsa:6727'], '200008_s_at': ['hsa:2665'], '200009_at': ['hsa:2665'], '200010_at': ['hsa:6135'], '200011_s_at': ['hsa:377'], '200012_x_at': ['hsa:6144', 'hsa:619499', 'hsa:26771', 'hsa:100131205'], '2

In [170]:
# transpose dataframe so that the columns indicate the genes
# and rows correspond to samples (class: ERpos or ERneg)
genes=gse2034['Gene']
gse2034.drop('KEGG-ID', inplace=True, axis=1)
gse2034=np.transpose(gse2034.iloc[:,1:])
gse2034.columns=genes.values.tolist()
gse2034.columns

Index(['1007_s_at', '1007_s_at', '1053_at', '117_at', '121_at', '1255_g_at',
       '1294_at', '1316_at', '1320_at', '1405_i_at',
       ...
       'AFFX-HSAC07/X00351_5_at', 'AFFX-HSAC07/X00351_M_at',
       'AFFX-HUMGAPDH/M33197_3_at', 'AFFX-HUMGAPDH/M33197_5_at',
       'AFFX-HUMGAPDH/M33197_M_at', 'AFFX-HUMISGF3A/M97935_3_at',
       'AFFX-HUMISGF3A/M97935_5_at', 'AFFX-HUMISGF3A/M97935_MA_at',
       'AFFX-HUMISGF3A/M97935_MB_at', 'AFFX-HUMRGE/M10098_5_at'],
      dtype='object', length=22645)

In [174]:
# Because one gene might correspond to more than one KEGG-IDs, we calculate the average (or max)
# value and get the following simplified dataframe
gse2034=gse2034.groupby(level=0,axis=1).mean()
gse2034

1007_s_at  1053_at  117_at  121_at  1255_g_at  1294_at  1316_at  \
ERpos     3848.1    228.9   213.1  1009.4       31.8    551.5    176.7   
ERpos     3848.1    228.9   213.1  1009.4       31.8    551.5    176.7   
ERpos     3848.1    228.9   213.1  1009.4       31.8    551.5    176.7   
ERneg     4043.7    398.7   312.4  1104.4      108.2    568.5    187.7   
ERpos     3848.1    228.9   213.1  1009.4       31.8    551.5    176.7   
...          ...      ...     ...     ...        ...      ...      ...   
ERpos     3848.1    228.9   213.1  1009.4       31.8    551.5    176.7   
ERpos     3848.1    228.9   213.1  1009.4       31.8    551.5    176.7   
ERpos     3848.1    228.9   213.1  1009.4       31.8    551.5    176.7   
ERneg     4043.7    398.7   312.4  1104.4      108.2    568.5    187.7   
ERpos     3848.1    228.9   213.1  1009.4       31.8    551.5    176.7   

       1320_at  1405_i_at  1431_at  ...  AFFX-HSAC07/X00351_5_at  \
ERpos     11.9      309.3     49.9  ...                   7287.1   
ERpos     11.9      309.3     49.9  ...                   7287.1   
ERpos     11.9      309.3     49.9  ...                   7287.1   
ERneg     42.1      899.1     90.7  ...                  16474.5   
ERpos     11.9      309.3     49.9  ...                   7287.1   
...        ...        ...      ...  ...                      ...   
ERpos     11.9      309.3     49.9  ...                   7287.1   
ERpos     11.9      309.3     49.9  ...                   7287.1   
ERpos     11.9      309.3     49.9  ...                   7287.1   
ERneg     42.1      899.1     90.7  ...                  16474.5   
ERpos     11.9      309.3     49.9  ...                   7287.1   

       AFFX-HSAC07/X00351_M_at  AFFX-HUMGAPDH/M33197_3_at  \
ERpos                  18021.8                    19418.9   
ERpos                  18021.8                    19418.9   
ERpos                  18021.8                    19418.9   
ERneg                  38913.5                    23342.8   
ERpos                  18021.8                    19418.9   
...                        ...                        ...   
ERpos                  18021.8                    19418.9   
ERpos                  18021.8                    19418.9   
ERpos                  18021.8                    19418.9   
ERneg                  38913.5                    23342.8   
ERpos                  18021.8                    19418.9   

       AFFX-HUMGAPDH/M33197_5_at  AFFX-HUMGAPDH/M33197_M_at  \
ERpos                     7449.3                    14027.7   
ERpos                     7449.3                    14027.7   
ERpos                     7449.3                    14027.7   
ERneg                     9439.4                    18474.2   
ERpos                     7449.3                    14027.7   
...                          ...                        ...   
ERpos                     7449.3                    14027.7   
ERpos                     7449.3                    14027.7   
ERpos                     7449.3                    14027.7   
ERneg                     9439.4                    18474.2   
ERpos                     7449.3                    14027.7   

       AFFX-HUMISGF3A/M97935_3_at  AFFX-HUMISGF3A/M97935_5_at  \
ERpos                      2908.8                        29.8   
ERpos                      2908.8                        29.8   
ERpos                      2908.8                        29.8   
ERneg                      3496.5                        71.1   
ERpos                      2908.8                        29.8   
...                           ...                         ...   
ERpos                      2908.8                        29.8   
ERpos                      2908.8                        29.8   
ERpos                      2908.8                        29.8   
ERneg                      3496.5                        71.1   
ERpos                      2908.8                        29.8   

       AFFX-HUMISGF3A/M97935_M

### 1.2. All-subpaths

In [12]:
all_subpaths_raw = pd.read_csv('Data/All-subpaths.zip')
all_subpaths_raw

SubPathID
0      208200_at#hsa:3552 210118_s_at#hsa:3552 205067...
1      208438_s_at#hsa:2268 208018_s_at#hsa:3055 2026...
2      207072_at#hsa:8807 206618_at#hsa:8809 -->20923...
3      206109_at#hsa:2523 208505_s_at#hsa:2524 210608...
4      213464_at#hsa:25759 noProbe#hsa:399694 206330_...
...                                                  ...
41604  206890_at#hsa:3594-->206118_at#hsa:6775-->2078...
41605  221271_at#hsa:59067-->219971_at#hsa:50615 2216...
41606  219971_at#hsa:50615 221658_s_at#hsa:50615-->20...
41607  216857_at#hsa:51561 217326_x_at#hsa:51561 2173...
41608  200887_s_at#hsa:6772 209969_s_at#hsa:6772 AFFX...

[41609 rows x 1 columns]

In [ ]:
# Split each subpath, get the max length of the paths and create the dataframe with NaN values for pathways with 
# length smaller that the max length.
max_len=0
all_subpaths_list=[]
for x in all_subpaths_raw['SubPathID']:
    # Subpaths are splitted based on the activation symbol (-->). Inhibition is handled next. 
    tmp=x.split(relation_dict['Activation']) 
    all_subpaths_list.append(tmp)
    if(len(tmp)>max_len):
        max_len=len(tmp)
        
all_subpaths = pd.DataFrame(np.nan, index=np.arange(all_subpaths_raw.size), columns=list(range(max_len)))
for x in range(len(all_subpaths_list)):
    for y in range(len(all_subpaths_list[x])):
        all_subpaths.loc[x,y]=all_subpaths_list[x][y]

In [ ]:
all_subpaths # rows are the subpaths and columns are the edges (containing one or more genes)

### 1.3. Selected

In [23]:
selected_raw = pd.read_csv('Data/Selected.zip', compression='zip', header=0, sep='\t', quotechar='"')[['SubPathID']]
selected_raw

SubPathID
0      208200_at#hsa:3552 210118_s_at#hsa:3552 205067...
1      208438_s_at#hsa:2268 208018_s_at#hsa:3055 2026...
2      207072_at#hsa:8807 206618_at#hsa:8809 -->20923...
3      206109_at#hsa:2523 208505_s_at#hsa:2524 210608...
4      213464_at#hsa:25759 noProbe#hsa:399694 206330_...
...                                                  ...
41603  206890_at#hsa:3594-->206118_at#hsa:6775-->2078...
41604  221271_at#hsa:59067-->219971_at#hsa:50615 2216...
41605  219971_at#hsa:50615 221658_s_at#hsa:50615-->20...
41606  216857_at#hsa:51561 217326_x_at#hsa:51561 2173...
41607  200887_s_at#hsa:6772 209969_s_at#hsa:6772 AFFX...

[41608 rows x 1 columns]

## 2. Discretization process
Transform gene expression values into high (expressed / up-regulated) or low (not-expressed / down-regulated) gene expression binary equivalents

### 2.1. The expression values of a gene over the total number of input samples are sorted in descending order;

In [76]:
genes_dis = pd.DataFrame(np.nan, index=gse2034.columns, columns=['Expression value'])
genes_dis['Expression value']=gse2034.sum()/gse2034.shape[0] # sum of expression values of a gene / total number of samples
genes_dis=genes_dis.sort_values(by=['Expression value'],ascending=False)
genes_dis

Expression value
210646_x_at      48931.611538
207783_x_at      47760.203846
212869_x_at      45788.103846
208825_x_at      43967.907692
201492_s_at      43252.146154
...                       ...
211213_at            1.573077
215309_at            1.188462
205421_at            1.130769
204704_s_at          1.030769
215112_x_at          0.823077

[20902 rows x 1 columns]

### 2.2. The midpoints between each two consecutive values are calculated;

In [77]:
def midpoint(num1,num2):
    return (num1+num2)/2

midpoints_dict={} # Key corresponds to the position of the first gene. The second gene is in the next position (i+1).
for i in range(genes_dis.shape[0]-1):
    midpoints_dict.update({i:midpoint(genes_dis.iloc[i]['Expression value'],genes_dis.iloc[i+1]['Expression value'])})

midpoints_dict

{0: 48345.90769230768,
 1: 46774.15384615384,
 2: 44878.00576923076,
 3: 43610.02692307692,
 4: 43160.05,
 5: 42642.30769230769,
 6: 41937.725,
 7: 41548.7,
 8: 41379.399999999994,
 9: 41246.6673076923,
 10: 40503.536538461536,
 11: 39740.715384615374,
 12: 39501.851923076916,
 13: 39023.592307692306,
 14: 38444.06538461537,
 15: 38107.65192307692,
 16: 37854.41346153847,
 17: 37012.73653846154,
 18: 36193.81153846154,
 19: 35968.015384615384,
 20: 35793.876923076925,
 21: 35633.09423076923,
 22: 35558.99038461539,
 23: 35507.43653846154,
 24: 35439.03269230769,
 25: 35412.56153846154,
 26: 35263.99038461539,
 27: 34946.3673076923,
 28: 34727.14423076922,
 29: 34663.49999999999,
 30: 34424.76346153845,
 31: 34122.18076923076,
 32: 34011.855769230766,
 33: 33818.613461538465,
 34: 33216.94807692308,
 35: 32724.57884615385,
 36: 32571.01346153846,
 37: 32356.69038461538,
 38: 32210.365384615383,
 39: 31987.77115384616,
 40: 31720.915384615386,
 41: 31599.007692307692,
 42: 31435.93653846

### 2.3. For each midpoint, μi, the Information Gain (IG) of the system is computed. Let IG(S,μi) to denote the IG of the system for midpoint μi.

In [78]:
classes=sorted(set(gse2034.index)) # Τhe classes to which a sample may belong
samples=gse2034.index # the samples class

# Calculate the proportion of samples in S that belong in Class C
def P(C,S):
    return list(S).count(C)/len(S)

def E(S,m=1):
    # m not given: calculate the entropy of the system taking into account the prior assignment of sample cases into phenotype classes
    # m given: calculate the respective entropy of the system taking into account its division into subgroups around midpoint μi
    tmp=0
    for c in classes:
        # P(c,S) must be greater than zero
        tmp+=P(c,S)*math.log(P(c,S))/m
    return -(tmp)

entropy=E(samples)
print('Dataset Entropy: %.3f bits' % entropy)

Dataset Entropy: 0.582 bits


In [79]:
# Calculate the Information Gain (IG) of the system
def IG(S,m):
    return E(S)-E(S,m)

information_gain=[]
for m in list(midpoints_dict.values()):
    information_gain.append(IG(samples,m))
print('Information Gain: '+str(information_gain))

Information Gain: [0.582480195455803, 0.5824797905919346, 0.5824792644257821, 0.5824788870428537, 0.5824787477874378, 0.582478583924339, 0.5824783544275832, 0.5824782243790821, 0.5824781670195665, 0.5824781217199007, 0.5824778626162204, 0.5824775865684465, 0.5824774979372257, 0.5824773172160036, 0.5824770922032104, 0.5824769584445176, 0.5824768561879756, 0.5824765062687137, 0.5824761501877475, 0.5824760491564591, 0.5824759703685393, 0.5824758969396149, 0.5824758628730817, 0.5824758390892143, 0.5824758074249435, 0.5824757951385671, 0.5824757258381503, 0.5824755757077289, 0.5824754704860304, 0.5824754396890806, 0.5824753231515897, 0.5824751731048768, 0.5824751177320143, 0.5824750198717836, 0.5824747078897048, 0.5824744440456829, 0.5824743601232355, 0.5824742416654206, 0.5824741598850762, 0.5824740340434218, 0.5824738808510813, 0.5824738100072401, 0.5824737143831219, 0.5824736308465888, 0.5824734728316598, 0.5824733161094879, 0.5824732837809045, 0.5824732337597643, 0.5824731982262168, 0.5

In [80]:
# The midpoint with the highest information gain is selected as the discretization point
max_value = max(information_gain)
max_mid_pos = information_gain.index(max(information_gain))
dis_point=midpoints_dict.get(max_mid_pos)
print('Discretization point: %.3f' %dis_point)

Discretization point: 48345.908


### 2.4. The sample cases with expression values lower than the discretization point are assigned the '0' value (meaning that the gene is under-expressed), and the sample cases with expression values bigger that the discretization point are assigned the '1' value (the gene is over-expressed).
The discretization process is applied for each gene separately, and the final dataset is a matrix of discretized, actually binarized, values.

In [81]:
gse2034_dis=gse2034.copy()
gse2034_dis[gse2034_dis<dis_point]=0 # under-expressed
gse2034_dis[gse2034_dis>=dis_point]=1 # over-expressed
gse2034_dis=gse2034_dis.astype('int')
gse2034_dis

1007_s_at  1053_at  117_at  121_at  1255_g_at  1294_at  1316_at  \
ERpos          0        0       0       0          0        0        0   
ERpos          0        0       0       0          0        0        0   
ERpos          0        0       0       0          0        0        0   
ERneg          0        0       0       0          0        0        0   
ERpos          0        0       0       0          0        0        0   
...          ...      ...     ...     ...        ...      ...      ...   
ERpos          0        0       0       0          0        0        0   
ERpos          0        0       0       0          0        0        0   
ERpos          0        0       0       0          0        0        0   
ERneg          0        0       0       0          0        0        0   
ERpos          0        0       0       0          0        0        0   

       1320_at  1405_i_at  1431_at  ...  AFFX-HSAC07/X00351_5_at  \
ERpos        0          0        0  ...                        0   
ERpos        0          0        0  ...                        0   
ERpos        0          0        0  ...                        0   
ERneg        0          0        0  ...                        0   
ERpos        0          0        0  ...                        0   
...        ...        ...      ...  ...                      ...   
ERpos        0          0        0  ...                        0   
ERpos        0          0        0  ...                        0   
ERpos        0          0        0  ...                        0   
ERneg        0          0        0  ...                        0   
ERpos        0          0        0  ...                        0   

       AFFX-HSAC07/X00351_M_at  AFFX-HUMGAPDH/M33197_3_at  \
ERpos                        0                          0   
ERpos                        0                          0   
ERpos                        0                          0   
ERneg                        0                          0   
ERpos                        0                          0   
...                        ...                        ...   
ERpos                        0                          0   
ERpos                        0                          0   
ERpos                        0                          0   
ERneg                        0                          0   
ERpos                        0                          0   

       AFFX-HUMGAPDH/M33197_5_at  AFFX-HUMGAPDH/M33197_M_at  \
ERpos                          0                          0   
ERpos                          0                          0   
ERpos                          0                          0   
ERneg                          0                          0   
ERpos                          0                          0   
...                          ...                        ...   
ERpos                          0                          0   
ERpos                          0                          0   
ERpos                          0                          0   
ERneg                          0                          0   
ERpos                          0                          0   

       AFFX-HUMISGF3A/M97935_3_at  AFFX-HUMISGF3A/M97935_5_at  \
ERpos                           0                           0   
ERpos                           0                           0   
ERpos                           0                           0   
ERneg                           0                           0   
ERpos                           0                           0   
...                           ...                         ...   
ERpos                           0                           0   
ERpos                           0                           0   
ERpos                           0                           0   
ERneg                           0                           0   
ERpos                           0                           0   

       AFFX-HUMISGF3A/M97935_M

## 3. Matching sub-paths with gene expression profiles

In [31]:
from itertools import chain

# Make the selected dataset easier to understand, by splitting each pathway based on their nodes and edges
def calc_pathway(data):
    s=[]
    cnt_act=len(data.split(relations_dict['Activation']))
    cnt_tmp=1
    # If there is at least one Activation relation split data
    if(cnt_act>0):
        for e in data.split(relations_dict['Activation']):
            if e:
                s.append(e)
                # Remove the final relation
                if(cnt_tmp<cnt_act):
                    s.append(relations_dict['Activation'])
                cnt_tmp+=1

    for i in range(len(s)):
        tmp_s=[]
        cnt_inh=len(s[i].split(relations_dict['Inhibition']))
        cnt_tmp=1
        # If there is at least one Inhibition relation split data
        if(cnt_inh>0):
            for e in s[i].split(relations_dict['Inhibition']):
                if e:
                    tmp_s.append(e)
                    # Remove the final relation
                    if(cnt_tmp<cnt_inh):
                        tmp_s.append(relations_dict['Inhibition'])
                    cnt_tmp+=1
            s[i]=tmp_s
            
    return list(chain.from_iterable(s))

data=[]
for row in selected_raw['SubPathID']:
    data.append(calc_pathway(row))

data

[['208200_at#hsa:3552 210118_s_at#hsa:3552 205067_at#hsa:3553 39402_at#hsa:3553 ',
  '-->',
  '202948_at#hsa:3554 215561_s_at#hsa:3554 205403_at#hsa:7850 211372_s_at#hsa:7850 ',
  '-->',
  '203901_at#hsa:10454',
  '-->',
  '206853_s_at#hsa:6885 206854_s_at#hsa:6885 211536_x_at#hsa:6885 211537_x_at#hsa:6885',
  '-->',
  '209666_s_at#hsa:1147 209341_s_at#hsa:3551 209342_s_at#hsa:3551 211027_s_at#hsa:3551 209929_s_at#hsa:8517 36004_at#hsa:8517 '],
 ['208438_s_at#hsa:2268 208018_s_at#hsa:3055 202625_at#hsa:4067 202626_s_at#hsa:4067 210754_s_at#hsa:4067 213324_at#hsa:6714 221281_at#hsa:6714 221284_s_at#hsa:6714 ',
  '-->',
  '207821_s_at#hsa:5747 208820_at#hsa:5747'],
 ['207072_at#hsa:8807 206618_at#hsa:8809 ',
  '-->',
  '209239_at#hsa:4790 201783_s_at#hsa:5970 209878_s_at#hsa:5970 '],
 ['206109_at#hsa:2523 208505_s_at#hsa:2524 210608_s_at#hsa:2524 ',
  '-->',
  '214088_s_at#hsa:2525 216010_x_at#hsa:2525'],
 ['213464_at#hsa:25759 noProbe#hsa:399694 206330_s_at#hsa:53358 201469_s_at#hsa:646

In [32]:
selected=pd.DataFrame(data).fillna(value=np.nan) # Rows: pathways, Cols: edges and nodes

# Change index names
index= ['P'+str(i) for i in range(selected.shape[0])]
selected.index=index

selected

0    1   \
P0      208200_at#hsa:3552 210118_s_at#hsa:3552 205067...  -->   
P1      208438_s_at#hsa:2268 208018_s_at#hsa:3055 2026...  -->   
P2                 207072_at#hsa:8807 206618_at#hsa:8809   -->   
P3      206109_at#hsa:2523 208505_s_at#hsa:2524 210608...  -->   
P4      213464_at#hsa:25759 noProbe#hsa:399694 206330_...  -->   
...                                                   ...  ...   
P41603                                 206890_at#hsa:3594  -->   
P41604                                221271_at#hsa:59067  -->   
P41605          219971_at#hsa:50615 221658_s_at#hsa:50615  -->   
P41606  216857_at#hsa:51561 217326_x_at#hsa:51561 2173...  -->   
P41607  200887_s_at#hsa:6772 209969_s_at#hsa:6772 AFFX...  -->   

                                                       2    3   \
P0      202948_at#hsa:3554 215561_s_at#hsa:3554 205403...  -->   
P1                207821_s_at#hsa:5747 208820_at#hsa:5747  NaN   
P2      209239_at#hsa:4790 201783_s_at#hsa:5970 209878...  NaN   
P3              214088_s_at#hsa:2525 216010_x_at#hsa:2525  NaN   
P4                                   215075_s_at#hsa:2885  -->   
...                                                   ...  ...   
P41603                                 206118_at#hsa:6775  -->   
P41604          219971_at#hsa:50615 221658_s_at#hsa:50615  -->   
P41605            208991_at#hsa:6774 208992_s_at#hsa:6774  -->   
P41606                                 206890_at#hsa:3594  -->   
P41607                                220684_at#hsa:30009  -->   

                                               4    5   \
P0                            203901_at#hsa:10454  -->   
P1                                            NaN  NaN   
P2                                            NaN  NaN   
P3                                            NaN  NaN   
P4        207112_s_at#hsa:2549 214987_at#hsa:2549  -->   
...                                           ...  ...   
P41603                         207849_at#hsa:3558  NaN   
P41604    208991_at#hsa:6774 208992_s_at#hsa:6774  -->   
P41605  210426_x_at#hsa:6095 210479_s_at#hsa:6095  -->   
P41606    208991_at#hsa:6774 208992_s_at#hsa:6774  -->   
P41607                         206999_at#hsa:3595  -->   

                                                       6    7   \
P0      206853_s_at#hsa:6885 206854_s_at#hsa:6885 2115...  -->   
P1                                                    NaN  NaN   
P2                                                    NaN  NaN   
P3                                                    NaN  NaN   
P4      220566_at#hsa:23533 204369_at#hsa:5290 212688_...  -->   
...                                                   ...  ...   
P41603                                                NaN  NaN   
P41604          210426_x_at#hsa:6095 210479_s_at#hsa:6095  -->   
P41605  noProbe#hsa:112744 208402_at#hsa:3605 216876_s...  NaN   
P41606                                221271_at#hsa:59067  -->   
P41607                                 206118_at#hsa:6775  -->   

                                                       8    9   ...   47   48  \
P0      209666_s_at#hsa:1147 209341_s_at#hsa:3551 2093...  NaN  ...  NaN  NaN   
P1                                                    NaN  NaN  ...  NaN  NaN   
P2                                                    NaN  NaN  ...  NaN  NaN   
P3                                                    NaN  NaN  ...  NaN  NaN   
P4      212607_at#hsa:10000 212609_s_at#hsa:10000 2193...  --|  ...  NaN  NaN   
...                                                   ...  ...  ...  ...  ...   
P41603                                                NaN  NaN  ...  NaN  NaN   
P41604  noProbe#hsa:112744 208402_at#hsa:3605 216876_s...  NaN  ...  NaN  NaN   
P41605                                                NaN  NaN  ...  NaN  NaN   
P41606          219971_at#hsa:50615 221658_s_at#hsa:50615  NaN  ...  NaN  NaN   
P41607                                 207849_at#hsa:3558  NaN  ...  NaN  NaN   

      

In [285]:
gene_expression_profiles=selected.copy()
gene_expression_profiles

0    1   \
P0      208200_at#hsa:3552 210118_s_at#hsa:3552 205067...  -->   
P1      208438_s_at#hsa:2268 208018_s_at#hsa:3055 2026...  -->   
P2                 207072_at#hsa:8807 206618_at#hsa:8809   -->   
P3      206109_at#hsa:2523 208505_s_at#hsa:2524 210608...  -->   
P4      213464_at#hsa:25759 noProbe#hsa:399694 206330_...  -->   
...                                                   ...  ...   
P41603                                 206890_at#hsa:3594  -->   
P41604                                221271_at#hsa:59067  -->   
P41605          219971_at#hsa:50615 221658_s_at#hsa:50615  -->   
P41606  216857_at#hsa:51561 217326_x_at#hsa:51561 2173...  -->   
P41607  200887_s_at#hsa:6772 209969_s_at#hsa:6772 AFFX...  -->   

                                                       2    3   \
P0      202948_at#hsa:3554 215561_s_at#hsa:3554 205403...  -->   
P1                207821_s_at#hsa:5747 208820_at#hsa:5747  NaN   
P2      209239_at#hsa:4790 201783_s_at#hsa:5970 209878...  NaN   
P3              214088_s_at#hsa:2525 216010_x_at#hsa:2525  NaN   
P4                                   215075_s_at#hsa:2885  -->   
...                                                   ...  ...   
P41603                                 206118_at#hsa:6775  -->   
P41604          219971_at#hsa:50615 221658_s_at#hsa:50615  -->   
P41605            208991_at#hsa:6774 208992_s_at#hsa:6774  -->   
P41606                                 206890_at#hsa:3594  -->   
P41607                                220684_at#hsa:30009  -->   

                                               4    5   \
P0                            203901_at#hsa:10454  -->   
P1                                            NaN  NaN   
P2                                            NaN  NaN   
P3                                            NaN  NaN   
P4        207112_s_at#hsa:2549 214987_at#hsa:2549  -->   
...                                           ...  ...   
P41603                         207849_at#hsa:3558  NaN   
P41604    208991_at#hsa:6774 208992_s_at#hsa:6774  -->   
P41605  210426_x_at#hsa:6095 210479_s_at#hsa:6095  -->   
P41606    208991_at#hsa:6774 208992_s_at#hsa:6774  -->   
P41607                         206999_at#hsa:3595  -->   

                                                       6    7   \
P0      206853_s_at#hsa:6885 206854_s_at#hsa:6885 2115...  -->   
P1                                                    NaN  NaN   
P2                                                    NaN  NaN   
P3                                                    NaN  NaN   
P4      220566_at#hsa:23533 204369_at#hsa:5290 212688_...  -->   
...                                                   ...  ...   
P41603                                                NaN  NaN   
P41604          210426_x_at#hsa:6095 210479_s_at#hsa:6095  -->   
P41605  noProbe#hsa:112744 208402_at#hsa:3605 216876_s...  NaN   
P41606                                221271_at#hsa:59067  -->   
P41607                                 206118_at#hsa:6775  -->   

                                                       8    9   ...   47   48  \
P0      209666_s_at#hsa:1147 209341_s_at#hsa:3551 2093...  NaN  ...  NaN  NaN   
P1                                                    NaN  NaN  ...  NaN  NaN   
P2                                                    NaN  NaN  ...  NaN  NaN   
P3                                                    NaN  NaN  ...  NaN  NaN   
P4      212607_at#hsa:10000 212609_s_at#hsa:10000 2193...  --|  ...  NaN  NaN   
...                                                   ...  ...  ...  ...  ...   
P41603                                                NaN  NaN  ...  NaN  NaN   
P41604  noProbe#hsa:112744 208402_at#hsa:3605 216876_s...  NaN  ...  NaN  NaN   
P41605                                                NaN  NaN  ...  NaN  NaN   
P41606          219971_at#hsa:50615 221658_s_at#hsa:50615  NaN  ...  NaN  NaN   
P41607                                 207849_at#hsa:3558  NaN  ...  NaN  NaN   

      

In [256]:
import statistics

expr_prof_tmp={}
for row in range(gene_expression_profiles.shape[0]):
    row_tmp=[]
    path_tmp=gene_expression_profiles.iloc[row][~gene_expression_profiles.iloc[row].isnull()]
    expr_prof_tmp[row]=[]
    
    for i in path_tmp[::2]:
        node_genes=[(g.split('#')) for g in list(filter(None,i.split(' ')))] # Get genes of node
        node_genes=list(filter(None, node_genes))
        tmp_expr_vals=[]
        
        for n in node_genes:
            # Check if gene exists in gse2034 dataset or KEGG-ID with noProbe correspondes to specific gene from gse2034 dataset
            if(n[0]=='noProbe'):
                if(not(n[1] in gene_dict.values())):
                    tmp_expr_vals.append(0)
                    continue
            if(len(n)==1):
                if(not(n in gene_dict.values())):
                    tmp_expr_vals.append(0)
                    continue
            tmp_expr_vals.append(genes_dis.loc[n[0]]["Expression value"])
    
        if(len(tmp_expr_vals)>0):
            expr_prof_tmp[row].append(statistics.median(tmp_expr_vals))
              
expr_prof_tmp

[54.12692307692308]


In [286]:
#gene_expression_profiles
for row in range(gene_expression_profiles.shape[0]):
    cnt=0
    print(expr_prof_tmp[row])
    tmp=expr_prof_tmp[row]
    for col in range(0,len(gene_expression_profiles.iloc[row][~gene_expression_profiles.iloc[row].isnull()]),2):
        gene_expression_profiles.iloc[row,col]=tmp[cnt]
        cnt+=1

[186.22307692307692, 62.84423076923077, 166.43076923076922, 518.7211538461538, 421.1846153846154]
[234.16923076923075, 975.1403846153846]
[125.02115384615382, 815.4423076923076]
[299.9538461538461, 216.58653846153842]
[236.8538461538462, 885.823076923077, 118.37500000000003, 284.14615384615394, 270.6903846153846, 1310.2076923076922]
[130.69230769230768, 96.58461538461538]
[83.63846153846154, 23.60769230769231, 1436.0384615384614, 1315.9384615384615, 1936.3307692307692]
[453.5692307692308, 0]
[3178.55, 31.053846153846145, 14.853846153846153, 101.95384615384614, 253.78653846153844, 133.58461538461543, 720.3307692307693]
[10.819230769230769, 116.27692307692307]
[551.9538461538461, 108.2096153846154]
[901.0846153846155, 2732.292307692307, 1702.394230769231, 99.45, 192.00384615384613]
[158.09615384615387, 153.68846153846155]
[156.28076923076918, 105.52115384615385, 167.85769230769233, 1295.1307692307696]
[997.4192307692308, 978.3653846153845]
[113.36153846153844, 354.4461538461539, 342.3076

In [287]:
gene_expression_profiles # Πρέπει να βρω την median τιμή ως continuous values ή boolean;

0    1            2    3            4    5           6    7   \
P0       186.223077  -->    62.844231  -->   166.430769  -->  518.721154  -->   
P1       234.169231  -->   975.140385  NaN          NaN  NaN         NaN  NaN   
P2       125.021154  -->   815.442308  NaN          NaN  NaN         NaN  NaN   
P3       299.953846  -->   216.586538  NaN          NaN  NaN         NaN  NaN   
P4       236.853846  -->   885.823077  -->      118.375  -->  284.146154  -->   
...             ...  ...          ...  ...          ...  ...         ...  ...   
P41603    47.784615  -->   355.669231  -->    54.126923  NaN         NaN  NaN   
P41604    91.488462  -->   117.596154  -->  2760.082692  -->  178.907692  -->   
P41605   117.596154  -->  2760.082692  -->   178.907692  -->    2.234615  NaN   
P41606    89.773077  -->    47.784615  -->  2760.082692  -->   91.488462  -->   
P41607  1300.832692  -->   224.692308  -->        37.75  -->  355.669231  -->   

                8    9   ...   47   48   49   50   51   52   53   54   55   56  
P0      421.184615  NaN  ...  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
P1             NaN  NaN  ...  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
P2             NaN  NaN  ...  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
P3             NaN  NaN  ...  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
P4      270.690385  --|  ...  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
...            ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  
P41603         NaN  NaN  ...  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
P41604    2.234615  NaN  ...  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
P41605         NaN  NaN  ...  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
P41606  117.596154  NaN  ...  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  
P41607   54.126923  NaN  ...  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  

[41608 rows x 57 columns]

In [283]:
expr_prof_tmp

{0: [186.22307692307692,
  62.84423076923077,
  166.43076923076922,
  518.7211538461538,
  421.1846153846154],
 1: [234.16923076923075, 975.1403846153846],
 2: [125.02115384615382, 815.4423076923076],
 3: [299.9538461538461, 216.58653846153842],
 4: [236.8538461538462,
  885.823076923077,
  118.37500000000003,
  284.14615384615394,
  270.6903846153846,
  1310.2076923076922],
 5: [130.69230769230768, 96.58461538461538],
 6: [83.63846153846154,
  23.60769230769231,
  1436.0384615384614,
  1315.9384615384615,
  1936.3307692307692],
 7: [453.5692307692308, 0],
 8: [3178.55,
  31.053846153846145,
  14.853846153846153,
  101.95384615384614,
  253.78653846153844,
  133.58461538461543,
  720.3307692307693],
 9: [10.819230769230769, 116.27692307692307],
 10: [551.9538461538461, 108.2096153846154],
 11: [901.0846153846155,
  2732.292307692307,
  1702.394230769231,
  99.45,
  192.00384615384613],
 12: [158.09615384615387, 153.68846153846155],
 13: [156.28076923076918,
  105.52115384615385,
  167.